In [1]:
SELECT * FROM MyDatabase.dbo.rental_dataset

-- Data Cleaning 1 : Extract numbers from nvarchar monthly_rent column by creating function name dbo.UDF_ExtractNumbers. 
-- Source https://www.pragimtech.com/blog/sql-optimization/sql-function-to-get-number-from-string/
Select dbo.UDF_ExtractNumbers(monthly_rent) as rent from MyDatabase.dbo.rental_dataset

-- Data Cleaning 1 cont...: Add rent column that only has integer value instead or nvarchar for better analysis (aggregation)
ALTER TABLE MyDatabase.dbo.rental_dataset
ADD rent INT;

UPDATE MyDatabase.dbo.rental_dataset
SET rent = dbo.UDF_ExtractNumbers(monthly_rent)

-- Data cleaning 2: Identify duplicate  
SELECT ads_id , COUNT(*) AS duplicate_count
FROM MyDatabase.dbo.rental_dataset
GROUP BY ads_id
HAVING COUNT(*) > 1;

-- Data cleaning 2 cont...: See all column that has duplicate ads_id. 
SELECT rental_dataset.*
FROM MyDatabase.dbo.rental_dataset
JOIN (
    SELECT ads_id, COUNT(*) AS duplicate_count
    FROM MyDatabase.dbo.rental_dataset
    GROUP BY ads_id
    HAVING COUNT(*) > 1
) AS duplicates ON rental_dataset.ads_id = duplicates.ads_id;

-- Data cleaning 2 cont...: Delete the duplicate rows. 
WITH CTE AS (
SELECT *,
           ROW_NUMBER() OVER (PARTITION BY ads_id ORDER BY (SELECT NULL)) AS RowNum
FROM MyDatabase.dbo.rental_dataset
)
DELETE
FROM CTE
WHERE RowNum > 1;

-- Data cleaning 3: Separate the location into state column and city column
SELECT 
    location,
    SUBSTRING(location, 1, CHARINDEX(' - ', location) - 1) AS state,
    SUBSTRING(location, CHARINDEX(' - ', location) + 3, LEN(location)) AS city
FROM MyDatabase.dbo.rental_dataset;

-- Data cleaning 3 cont...: Add state and city column
ALTER TABLE MyDatabase.dbo.rental_dataset
ADD state VARCHAR(20);

ALTER TABLE MyDatabase.dbo.rental_dataset
DROP COLUMN state;

ALTER TABLE MyDatabase.dbo.rental_dataset
ADD city VARCHAR(100);

ALTER TABLE MyDatabase.dbo.rental_dataset
DROP COLUMN city;


UPDATE MyDatabase.dbo.rental_dataset
SET state = SUBSTRING(location, 1, CHARINDEX(' - ', location) - 1),
    city = SUBSTRING(location, CHARINDEX(' - ', location) + 3, LEN(location));

-- Data cleaning 4: add new integer column named size in sqft
ALTER TABLE MyDatabase.dbo.rental_dataset
ADD size_sqft INT;

UPDATE MyDatabase.dbo.rental_dataset
SET size_sqft = dbo.UDF_ExtractNumbers(size)

-- Data cleaning 5: Standardization (Delete all null values)
DELETE FROM MyDatabase.dbo.rental_dataset
WHERE
        ads_id IS NULL
      OR prop_name IS NULL
      OR completion_year IS NULL
      OR monthly_rent IS NULL
      OR location IS NULL
      OR property_type IS NULL
      OR rooms IS NULL
      OR parking IS NULL
      OR bathroom IS NULL
      OR size IS NULL
      OR furnished IS NULL
      OR facilities IS NULL
      OR additional_facilities IS NULL
      OR region IS NULL
      OR rent IS NULL
      OR state IS NULL
      OR city IS NULL
      OR size_sqft IS NULL

-- Data cleaning 6: Delete city that is irrelevant.

SELECT city, AVG(rent)
FROM MyDatabase.dbo.rental_dataset
GROUP BY city 
ORDER BY city -- to see which city that is irrelevant (eg: Got numbers instead of city name)

SELECT CAST( city AS VARCHAR)
FROM MyDatabase.dbo.rental_dataset -- make sure data type in city column is varchar. 

DELETE FROM MyDatabase.dbo.rental_dataset
WHERE city = '360'
OR city = '369'
OR city = '389'
OR city = '517'
OR city = '639' -- delete all irrelevant city rows. The one that are numbers instead of varchar. 

-- Data cleaning 7: Order by and group by column one by one to see is there any irrelevant values. 

SELECT state, COUNT(*)
FROM MyDatabase.dbo.rental_dataset
GROUP BY state
ORDER BY state

(5975 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:01.599

ads_id prop_name completion_year monthly_rent location property_type rooms parking bathroom size furnished facilities additional_facilities region rent state city size_sqft 100323185 The Hipster @ Taman Desa 2022 RM 4 200 per month Kuala Lumpur - Taman Desa Condominium 5 2 6 1842 sq.ft. Fully Furnished Minimart, Gymnasium, Security, Playground, Swimming Pool, Parking, Lift, Barbeque area, Multipurpose hall, Jogging Track Air-Cond, Cooking Allowed, Washing Machine Kuala Lumpur 4200 Kuala Lumpur Taman Desa 1842 100191767 Sentul Point Suite Apartment 2020 RM 1 700 per month Kuala Lumpur - Sentul Apartment 2 1 2 743 sq.ft. Partially Furnished Parking, Playground, Swimming Pool, Squash Court, Security, Minimart, Gymnasium, Lift Cooking Allowed, Near KTM/LRT, Washing Machine Kuala Lumpur 1700 Kuala Lumpur Sentul 743 100322885 Arte Plus Jalan Ampang 2018 RM 1 550 per month Kuala Lumpur - Ampang Service Residence 1 1 1 700 sq.ft. Fully Furnished Parking, Gymnasium, Playground, Security, Lift, Swimming Pool, Multipurpose hall Air-Cond, Cooking Allowed, Near KTM/LRT, Washing Machine Kuala Lumpur 1550 Kuala Lumpur Ampang 700 100322866 Nova I 2014 RM 1 400 per month Kuala Lumpur - Segambut Apartment 2 1 1 750 sq.ft. Fully Furnished Playground, Security, Parking, Lift, Swimming Pool Air-Cond, Cooking Allowed, Washing Machine, Near KTM/LRT Kuala Lumpur 1400 Kuala Lumpur Segambut 750 100322809 PV9 Residences @ Taman Melati 2022 RM 2 000 per month Kuala Lumpur - Setapak Service Residence 4 2 2 1100 sq.ft. Partially Furnished Parking, Security, Lift, Swimming Pool, Playground, Gymnasium, Barbeque area, Minimart, Multipurpose hall Air-Cond, Cooking Allowed, Near KTM/LRT, Washing Machine Kuala Lumpur 2000 Kuala Lumpur Setapak 1100 100322802 Arte Plus Jalan Ampang 2018 RM 1 500 per month Kuala Lumpur - Ampang Service Residence 1 1 1 700 sq.ft. Fully Furnished Gymnasium, Jogging Track, Playground, Parking, Security, Lift, Swimming Pool, Sauna, Barbeque area, Minimart, Multipurpose hall, Club house, Squash Court Air-Cond, Cooking Allowed, Washing Machine, Near KTM/LRT Kuala Lumpur 1500 Kuala Lumpur Ampang 700 87950203 Maxim Citilights 2017 RM 1 300 per month Kuala Lumpur - Sentul Service Residence 3 1 2 1009 sq.ft. Fully Furnished Minimart, Jogging Track, Playground, Swimming Pool, Multipurpose hall, Security, Lift, Parking, Gymnasium, Sauna, Barbeque area Air-Cond, Cooking Allowed, Washing Machine Kuala Lumpur 1300 Kuala Lumpur Sentul 1009 100322320 Legasi Kampong Bharu 2020 RM 3 200 per month Kuala Lumpur - KL City Apartment 3 1 2 950 sq.ft. Fully Furnished Lift, Squash Court, Jogging Track, Gymnasium, Playground, Security, Tennis Court, Swimming Pool, Parking, Minimart, Sauna, Barbeque area, Multipurpose hall Air-Cond, Cooking Allowed, Near KTM/LRT, Washing Machine, Internet Kuala Lumpur 3200 Kuala Lumpur KL City 950 100322311 Legasi Kampong Bharu 2020 RM 3 200 per month Kuala Lumpur - KL City Apartment 3 1 2 950 sq.ft. Fully Furnished Lift, Squash Court, Jogging Track, Gymnasium, Playground, Security, Tennis Court, Swimming Pool, Parking, Minimart, Sauna, Barbeque area, Multipurpose hall Air-Cond, Cooking Allowed, Near KTM/LRT, Washing Machine, Internet Kuala Lumpur 3200 Kuala Lumpur KL City 950 100322212 Majestic Maxim 2021 RM 1 400 per month Kuala Lumpur - Cheras Service Residence 2 2 2 650 sq.ft. Not Furnished Parking, Gymnasium, Jogging Track, Lift, Barbeque area, Security, Swimming Pool, Playground Air-Cond, Near KTM/LRT, Cooking Allowed Kuala Lumpur 1400 Kuala Lumpur Cheras 650 100322123 Majestic Maxim 2021 RM 1 099 per month Kuala Lumpur - Cheras Service Residence 2 1 2 650 sq.ft. Not Furnished Playground, Lift, Barbeque area, Security, Parking, Jogging Track, Gymnasium, Swimming Pool Air-Cond, Cooking Allowed, Near KTM/LRT Kuala Lumpur 1099 Kuala Lumpur Cheras 650 100310024 Majestic Maxim 2021 RM 1 099 per month Kuala Lumpur - Cheras Service Residence 2 1 2 650 sq.ft. Partially Furnished Security, Swimming Pool, Parking, Jogging Track, 

: Msg 4121, Level 16, State 1, Line 5
Cannot find either column "dbo" or the user-defined function or aggregate "dbo.UDF_ExtractNumbers", or the name is ambiguous.

No other irrelevant data.